In [1]:
!curl -O https://ai.stanford.edu/~amaas/data/sentiment/aclImdb_v1.tar.gz

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 80.2M  100 80.2M    0     0  4398k      0  0:00:18  0:00:17  0:00:01 5510k2M   69 55.4M    0     0  4094k      0  0:00:20  0:00:13  0:00:07 5411k    0  4444k      0  0:00:18  0:00:18 --:--:-- 5495k


In [9]:
!tar -xf aclImdb_v1.tar.gz

In [1]:
from utils import create_dataloaders
from torch import optim
import torch
import torch.nn as nn

/home/ivan/.local/lib/python3.10/site-packages/torchtext/vocab/__init__.py:4: UserWarning: 
/!\ IMPORTANT WARNING ABOUT TORCHTEXT STATUS /!\ 
Torchtext is deprecated and the last released version will be 0.18 (this one). You can silence this warning by calling the following at the beginnign of your scripts: `import torchtext; torchtext.disable_torchtext_deprecation_warning()`
  warnings.warn(torchtext._TORCHTEXT_DEPRECATION_MSG)
/home/ivan/.local/lib/python3.10/site-packages/torchtext/utils.py:4: UserWarning: 
/!\ IMPORTANT WARNING ABOUT TORCHTEXT STATUS /!\ 
Torchtext is deprecated and the last released version will be 0.18 (this one). You can silence this warning by calling the following at the beginnign of your scripts: `import torchtext; torchtext.disable_torchtext_deprecation_warning()`
  warnings.warn(torchtext._TORCHTEXT_DEPRECATION_MSG)
/home/ivan/.local/lib/python3.10/site-packages/torchtext/data/__init__.py:4: UserWarning: 
/!\ IMPORTANT WARNING ABOUT TORCHTEXT STATUS /!\ 
To

In [2]:
from transformer import Transformer

In [3]:
train_dir = "aclImdb/train"
train_dataloader, vocab = create_dataloaders(train_dir)

In [4]:
test_dir = "aclImdb/test"
test_dataloader, vocab = create_dataloaders(test_dir)

In [5]:
embed_dim = 128
num_heads = 2
dense_dim = 32

In [6]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [7]:
transformer = Transformer(embed_dim, dense_dim, num_heads, 20000).to(device)

rmsprop = optim.RMSprop(params=transformer.parameters(), lr=0.0001)
criterion = nn.BCELoss()

/home/ivan/.local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [11]:
for epoch in range(10):
    transformer.train()
    correct_predictions = 0
    total_predictions = 0


    for batch in train_dataloader:
        text, label = batch

        rmsprop.zero_grad()

        output = transformer(text.to(device))

        loss = criterion(output[:, 0], label.to(device).float())

        correct_predictions += (output[:, 0] > 0.5).eq(label.to(device)).sum().item()
        total_predictions += len(label)


        loss.backward()
        rmsprop.step()


    print(f"Epoch: {epoch+1}, Loss: {loss.item()}, Accuracy: {correct_predictions / total_predictions * 100}")


Epoch: 1, Loss: 0.7997985482215881, Accuracy: 62.29599999999999
Epoch: 2, Loss: 0.5285252332687378, Accuracy: 69.12
Epoch: 3, Loss: 0.42007097601890564, Accuracy: 74.516
Epoch: 4, Loss: 0.49864041805267334, Accuracy: 77.572


KeyboardInterrupt: 

In [13]:
correct_predictions = 0
total_predictions = 0
for batch in test_dataloader:
    text, label = batch

    output = transformer(text.to(device))

    loss = criterion(output[:, 0], label.to(device).float())

    correct_predictions += (output[:, 0] > 0.5).eq(label.to(device)).sum().item()
    total_predictions += len(label)

print(f"Loss: {loss.item()}, Accuracy: {correct_predictions / total_predictions * 100}")

Loss: 0.9633265733718872, Accuracy: 80.56400000000001


In [ ]:
for batch in train_dataloader:
    text, label = batch
    output = transformer(text.to(device))
    for i in range(0, len(label)):
        print(f"{label[i]} = {output[i,0]}")


1 = 0.24773773550987244 | 1 The nearest I ever came to seeing this was a clip shown at a Gerard Philippe exposition in Paris about two years ago. I had no interest in the remake 
0 = 0.6916823387145996 | 1 Farrah Fawcett gives the best performance by an actress on film in this gritty real life attempted rape thriller where she turns the tables & gives Ja
0 = 0.8283678889274597 | 1 This is probably Karisma at her best, apart from Zubeidaa. Nana Patekar also gives out his best, without even trying. The story is very good at times 
1 = 0.8967098593711853 | 1 "Twelve Monkeys" is odd and disturbing, yet being so clever and intelligent at the same time. It cleverly jumps between future and the past, and the s
1 = 0.3482578992843628 | 1 Was lucky enough to be an extra in this great film and loved every minute of the filming. Went to the premier in London and had a great chat to Phil, 
1 = 0.6614426374435425 | 1 I have never commented on a film before. I watched this movie with my girlfriend l